In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import warnings
warnings.filterwarnings('ignore')
import colorcet as cc
import datetime
from astropy.utils.data import get_pkg_data_filename
from astropy.io import fits

image_file = '/home/spectro/Documents/py/bbms/data/20210227daily.fits'
image_file = '/home/spectro/Documents/py/bbms/data/20170825_072442_072841_bbms_fast.fits'

fits.info(image_file)
image_data = fits.getdata(image_file, ext=1)
hdu = fits.open(image_file, ext=1)
d = hdu[1].data
fq_bbms =  d['FRQ']
tim_bbms = d['TIM'][0,:]
rcp_bbms = d['RCP']
lcp_bbms = d['LCP']

Ibbms =  rcp_bbms + lcp_bbms
Vbbms =  rcp_bbms - lcp_bbms

print(Ibbms.shape)
print(tim_bbms.max())
print(tim_bbms.min())
print(Ibbms.shape)
print(tim_bbms.shape)
print(fq_bbms.shape)

fq_bbms = fq_bbms/1e3 # from MHz to GHz

Ntim_bbms = tim_bbms.size
Nfq_bbms = fq_bbms.size
print(Ntim_bbms, Nfq_bbms)
img0 = np.empty((Ntim_bbms, Nfq_bbms), dtype=np.uint32)
print(img0.shape)
mIbbms = Ibbms.copy()

for j in range(Nfq_bbms):
    mbkg = np.median(Ibbms[j, 0:20])
    mIbbms[j,:] = mIbbms[j,:] - mbkg
    
print(mIbbms.max())
print(Ibbms.max())


Filename: /home/spectro/Documents/py/bbms/data/20170825_072442_072841_bbms_fast.fits
No.    Name      Ver    Type      Cards   Dimensions   Format
  0  PRIMARY       1 PrimaryHDU       4   ()      
  1  BBMS          1 BinTableHDU     17   26R x 4C   [1E, 21170D, 21170E, 21170E]   
(26, 21170)
26920.99702161685
26682.006108376198
(26, 21170)
(21170,)
(26,)
21170 26
(21170, 26)
150.86911
338.05225


In [2]:
# Bokeh Lib Visualization
# https://docs.bokeh.org/en/latest/docs/user_guide/tools.html
import bokeh as bk
from bokeh.plotting import figure, show, output_file, output_notebook, column
from bokeh.models import CrosshairTool, ColorBar, LinearColorMapper #, HoverTool, value, LabelSegt, Legend, ColumnDataSource, LinearColorMapper, BasicTicker, PrintfTickFormatter
from bokeh.layouts import gridplot

output_notebook() #output_file("plot.html")

TOOLS = "crosshair,hover,save,pan,box_zoom,reset,wheel_zoom,tap"
plot3 = figure(plot_height=300, x_range = [tim_bbms.min()-5, tim_bbms.max()+5], 
               y_range = [fq_bbms.min()-0.2,fq_bbms.max()+0.2], title=  "Dynamic spectrum", 
               tools=TOOLS, toolbar_location='above', sizing_mode = "scale_both") # plot_width=600,

color_mapper = LinearColorMapper(palette = cc.fire, low=mIbbms.min(), high= mIbbms.max()) # Plasma256, Magma256, Inferno256, Greys256, Cividis256
plot3.image(image = [mIbbms], x=tim_bbms.min(), y=fq_bbms.min(), 
            dw= tim_bbms.max()-tim_bbms.min() , dh=fq_bbms.max()-fq_bbms.min(),
             color_mapper = color_mapper, level="glyph") #  level="glyph, underlay, image"
xst = plot3.xaxis[0]
xst.axis_label = r"\[Time (s)\]"
plot3.yaxis[0].axis_label = r"$$ Frequency~(GHz) $$"
color_bar = ColorBar(color_mapper = color_mapper, label_standoff=12)
plot3.add_layout(color_bar, 'below')

w3 = figure(plot_height=200, plot_width=900, sizing_mode = "scale_both", 
            x_range = [tim_bbms.min()-5, tim_bbms.max()+5], background_fill_color="#ffffff", 
            tools=TOOLS, toolbar_location='above')
w3.line(tim_bbms,mIbbms[0,:], color="#000000", line_width = 1)

#show(column(plot3, w3))
#grid = gridplot([[s1, s2], [None, s3]], width=250, height=250)
#grid = gridplot([[plot3, w3], [None, None]], width=250, height=250)

crosshair = CrosshairTool(dimensions="both")
plot3.add_tools(crosshair)
w3.add_tools(crosshair)

#plot3.on_event('mouse')
#MouseEnter

grid = gridplot([[plot3], [w3]], width=900, height=300)
plot3.x_range = w3.x_range
show(grid)


Loading BokehJS ...